In [1]:
import pickle
import pandas as pd
import numpy as np
import re
from sklearn.feature_extraction.text import CountVectorizer
import matplotlib.pyplot as plt
from sklearn.preprocessing import Normalizer, StandardScaler
from tqdm import tqdm
import spacy
import requests
from scipy.spatial import distance
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import MinMaxScaler
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.naive_bayes import MultinomialNB
from sklearn.preprocessing import MaxAbsScaler
from sklearn.preprocessing import StandardScaler
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.svm import SVC
import pprint
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.metrics import accuracy_score
from sklearn.ensemble import RandomForestClassifier
from itertools import combinations

import nltk
from nltk import word_tokenize
from nltk.util import ngrams
from collections import Counter
from gensim.models import Word2Vec
import gensim
from random import sample 


# Before start - Spacy configuration (optional)
Model is saved in the file, but if you want to run it by your own, then you need to instal and configure Spacy on your machine

In [2]:
# environment preparation,morfeusz2 installation (in terminal)

# wget -O - http://download.sgjp.pl/apt/sgjp.gpg.key|sudo apt-key add -
# sudo apt-add-repository http://download.sgjp.pl/apt/ubuntu
# sudo apt update
# sudo apt install morfeusz2
# sudo apt install python3-morfeusz2

# spacy installation
# python3 -m pip install spacy

# morfeusz download
# http://morfeusz.sgjp.pl/download/

# spacy from IPI PAN
# https://github.com/ipipan/spacy-pl


# IPI PAN MODEL for polish language installation - hard to configurate, not recommended
# wget "http://zil.ipipan.waw.pl/SpacyPL?action=AttachFile&do=get&target=pl_spacy_model_morfeusz-0.1.3.tar.gz"
# python -m pip install pl_spacy_model_morfeusz-0.1.3.tar.gz


# if you have problem with module not found
# https://towardsdatascience.com/importerror-no-module-named-xyz-45e4a5339e1b


# official spacy model for polish language installation
# python -m spacy download pl_core_news_sm


# additional dependencies
# python3 -m pip install tqdm
# python3 -m pip install networkx

# spacy model linking
# python3 -m spacy link pl_core_news_sm pl_core_news_sm -f


# instalacja większego mdoelu
# python3 -m spacy download pl_core_news_lg
# python3 -m spacy link pl_core_news_lg pl_core_news_lg -f

## Spacy model load
First, we need to load pretrained statistical models for Polish

In [3]:
nlp = spacy.load("pl_core_news_lg")

## Dataset load
Next we load our preprocessed data

In [4]:
df_working = pd.read_pickle("data/df_working_pickle.pkl")
df_working

link  \
0                         /ravioli-z-cukinia-i-ricotta   
1     /galettes-bretonnes-czyli-nalesniki-po-bretonsku   
3                 /kluski-dyniowe-z-jogurtem-i-owocami   
4                          /kurczak-w-sosie-jogurtowym   
5      /koreanski-dosirak-ryz-z-przystawkami-w-pudelku   
...                                                ...   
2785                       /mus-czekoladowy-z-malinami   
2786                      /jablka-zapiekane-z-zurawina   
2787             /panna-cotta-waniliowa-z-owocami-lasu   
2788                       /letnie-owoce-pod-kruszonka   
2789                                  /mus-czekoladowy   

                                           recipe_name  meal_type_detailed  \
0                          Ravioli z cukinią i ricottą           Bez mięsa   
1     Galettes bretonnes, czyli naleśniki po bretońsku  Naleśniki na słono   
3                  Kluski dyniowe z jogurtem i owocami              Kluski   
4                           Kurczak w sosie jogurtowym             Kurczak   
5     Koreański dosirak – ryż z przystawkami w pudełku       Dania z ryżem   
...                                                ...                 ...   
2785                        Mus czekoladowy z malinami  Desery czekoladowe   
2786                       Jabłka zapiekane z żurawiną    Desery z owocami   
2787              Panna cotta waniliowa z owocami lasu    Desery z owocami   
2788                        Letnie owoce pod kruszonką    Desery z owocami   
2789                                   Mus czekoladowy  Desery czekoladowe   

                                            ingredients  \
0     cukinia – 1 szt., oliwa z oliwek – 1 łyżka, cz...   
1     mąka pszenna – 200 g, mąka gryczana – 100 g, m...   
3     dynia piżmowa – 1 szt., purée z dyni – 500 g, ...   
4     filet z piersi kurczaka – 400 g, oliwa z oliwe...   
5     ryż do sushi – 1 szklanka, woda (filtrowana lu...   
...                                                 ...   
2785  100 g świeżych lub mrożonych malin, 15 g cukru...   
2786  50 g białek jaj (2 białka jaj), 70 g cukru, 30...   
2787  250 ml śmietanki 30%, 250 ml mleka 3,2%, 80-10...   
2788  płatki owsiane Nordwaldtaler: 0,75 szklanki, m...   
2789  śmietanka Pilos 30%, mocno schłodzona: 300 ml,...   

                                           instructions meal_type  \
0      Przygotuj: tarkę o grubych i drobnych oczkach...    glowne   
1      Przygotuj: patelnię do naleśnik&#243;w tarkę ...    glowne   
3      Przygotuj: piekarnik rozgrzany do temperatury...    glowne   
4      Przygotuj: tarkę o drobnych oczkach ręcznik p...    glowne   
5      Przygotuj: pudełko do dosirak l&#243;d w kost...    glowne   
...                                                 ...       ...   
2785   Przygotowanie Żelatynę moczymy w zimnej wodzi...    desery   
2786   Masa bezowa Białka ubijamy na sztywną masę. D...    desery   
2787   Przygotowanie Mleko, śmietankę i cukier podgr...    desery   
2788   Przygotowanie Płatki i ziarno słonecznika pra...    desery   
2789   Przygotowanie Obie czekolady rozpuszczamy w k...    desery   

                                        raw_ingredients  \
0     cukinia – 1 szt., oliwa z oliwek – 1 łyżka, cz...   
1     mąka pszenna – 200 g, mąka gryczana – 100 g, m...   
3     dynia piżmowa – 1 szt., purée z dyni – 500 g, ...   
4     filet z piersi kurczaka – 400 g, oliwa z oliwe...   
5     ryż do sushi – 1 szklanka, woda (filtrowana lu...   
...                                                 ...   
2785  100 g świeżych lub mrożonych malin, 15 g cukru...   
2786  50 g białek jaj (2 białka jaj), 70 g cukru, 30...   
2787  250 ml śmietanki 30%, 250 ml mleka 3,2%, 80-10...   
2788  płatki owsiane Nordwaldtaler: 0,75 szklanki, m...   
2789  śmietanka Pilos 30%, mocno schłodzona: 300 ml,...   

                                    cleaned_ingredients  ingredients_count  \
0     cukinia, oliwa z oliwek, czosnek, świeża bazyl...                 22   
1     mąka ps

We will try a few approaches to find the best way to get alternatives for the ingredients used in a chosen recipe.
1. Spacy cosine similarity based on prelearned model
2. Similarity based on data from kuchnia lidla using Word2Vec 

To find recipe based on ingredients we will use simple classifier - logistic regression.

# 1. Spacy similarity module

First I defined the functions that will choose only nouns & adjectives and nouns only from the list of ingredients. It will help bringing same words to the based form. Problem with polish language is that verbs, adjectives and nouns conjugate (mąki' vs. 'mąka') and have singular/plural form ('jajko' vs. 'jajka'). This approach help cleaning  punctuation and other unnecessary words like verbs. Unfortunately, this approach is still not perfect, because we will get words like 'tabliczka'. It will also return unnecessary adjectives like 'dodatkowy' or  'dodatkowy', but adjectives might be useful for words like 'pszenny' in regards to type of flour. We will check both approaches - with adjectives and without them.

In [5]:
def lemantize(text):
    stoplist=['1', '½', 'łyżka', 'łyżeczka', 'pęczek', 'szczypta', 'szklanka', 'garść', 'sztuka', '%', '1/8','-0,5',
              '1/10', '1/2',  '1/3', '1/4', '10', '11/2', '150ml', '1:1', '1l', '1¼', '1½', '1¾', '1⅓',
              '2', '2:1', '2l', '2¼', '2¾', '3', '4', '5', '7x7', 'Celinka', 'Karol', 'Kinga', 'Małecki', 'Mistera', 'a','sól','pieprz','woda']
    lemats_list=[]
    for word in nlp(text):
        if word.pos_ == 'NOUN' or word.pos_ == 'ADJ':
            if word.lemma_ not in stoplist:
                lemats_list.append(word.lemma_)
    lemats_list = (', ').join(set(lemats_list))
    return lemats_list

def lemantize_nouns(text):
    stoplist=['1', '½', 'łyżka', 'łyżeczka', 'pęczek', 'szczypta', 'szklanka', 'garść', 'sztuka', '%', '1/8','-0,5',
              '1/10', '1/2',  '1/3', '1/4', '10', '11/2', '150ml', '1:1', '1l', '1¼', '1½', '1¾', '1⅓',
              '2', '2:1', '2l', '2¼', '2¾', '3', '4', '5', '7x7', 'Celinka', 'Karol', 'Kinga', 'Małecki', 'Mistera', 'a','sól','pieprz', 'woda']
    lemats_list=[]
    for word in nlp(text):
        if word.pos_ == 'NOUN':
            if word.lemma_ not in stoplist:
                lemats_list.append(word.lemma_)
    lemats_list = (', ').join(set(lemats_list))
    return lemats_list

In [6]:
%%time

df_working['lematized_ingredients']       = df_working.apply(lambda x: lemantize(x['cleaned_ingredients']),axis=1)
df_working['lematized_ingredients_nouns'] = df_working.apply(lambda x: lemantize_nouns(x['cleaned_ingredients']),axis=1)


CPU times: user 54.5 s, sys: 52.9 ms, total: 54.6 s
Wall time: 54.6 s


How the list of lematized ingredient looks?

In [7]:
df_working.iloc[0]['lematized_ingredients']

'czosnek, oliwa, winogrono, semolina, chili, pestka, tortowy, świeży, czarny, olej, masło, ricotta, parmezan, cukinia, mąka, ciepły, żółtko, ser, mielony, oliwka, bazylia, jajko'

In [8]:
df_working.iloc[0]['lematized_ingredients_nouns']

'pestka, czosnek, oliwa, ricotta, parmezan, winogrono, cukinia, oliwka, semolina, chili, mąka, bazylia, żółtko, jajko, masło, olej, ser'

In general, it looks promising. With more time, stoplist could have even more words, but majority of ingredients looks fine. Question that remains is whether we should use only nouns or adjectives as well. Unfortunately, even with regex usage, there is no simple method of keeping phrases like 'mąka pszenna' or 'śmietana 30%' as tokens. Therefore each word will be separate tokens. We will check both approaches and compare results.

But first, we need to get unique list of words for count vectoriser. It is needed for 2 reasons:
1. Dense matrix will be used for classification. Each ingredient will be separate feature for finding alternatives via classifier.
2. Additionally, it will be used in the function to find the recipe based on the ingredients that the user will pass to the program.

In [9]:
# create bag of words
words = df_working['lematized_ingredients'].tolist()

# keep only unique
unique_words = set((', ').join(words).split(', '))

# create columns with tokens
cv = CountVectorizer(vocabulary=unique_words)
df_ingredients_vectorized = cv.fit_transform(df_working['lematized_ingredients'])
df_ingredients_vectorized = pd.DataFrame(df_ingredients_vectorized.todense(), columns=unique_words)

len_of_unique_words = len(unique_words)
print(f'There are {len_of_unique_words} unique words in ingredients')

There are 1693 unique words in ingredients


In [10]:
df_ingredients_vectorized.columns

Index(['ocean', 'mein', 'bajgiel', 'wyszorowana', 'halloumi', 'cytrynowy',
       'gardis', 'bleu', 'rolada', 'siekanej',
       ...
       'superfoods', 'pasta', 'kefir', 'papierowy', 'jodowanej', 'ryż',
       'wieloziarnistego', 'łyzka', 'kapar', 'połówka'],
      dtype='object', length=1693)

If only nouns will be used, then tokens number drops

In [11]:
# create bag of words for nouns only
words_nouns = df_working['lematized_ingredients_nouns'].tolist()
# keep only unique
unique_words_nouns = set((', ').join(words_nouns).split(', '))

# create columns with tokens
cv_nouns = CountVectorizer(vocabulary=unique_words_nouns)
df_ingredients_vectorized_nouns = cv_nouns.fit_transform(df_working['lematized_ingredients_nouns'])
df_ingredients_vectorized_nouns = pd.DataFrame(df_ingredients_vectorized_nouns.todense(),
                                               columns=unique_words_nouns)

len_of_unique_words_nouns = len(unique_words_nouns)
print(f'There are {len_of_unique_words_nouns} unique words in ingredients')
print(f'Number of unique words drops by {(len_of_unique_words_nouns/len_of_unique_words-1)*100:.0f}% if only nouns are used')

There are 1191 unique words in ingredients
Number of unique words drops by -30% if only nouns are used


In [12]:
df_ingredients_vectorized_nouns.columns

Index(['gouda', 'kark', 'śledź', 'czosnek', 'mein', 'rum', 'gnocchi',
       'jalapeno', 'szarlotka', 'bajgiel',
       ...
       'rurka', 'kwaskowatość', 'kapar', 'połówka', 'środek', 'j',
       'nasmarowania', 'białka', 'awokado', 'tomato'],
      dtype='object', length=1191)

Now lets define the function that returns similarity matrix for a given list of ingredients. In our case, it will be all ingredients from the recipes.

In [13]:
def check_similarity(list_of_ingredients):
    similarity_dict_spacy = {}
    for i in list_of_ingredients:
        similarity_dict_spacy[i] = [nlp(i).similarity(nlp(j)) for j in list_of_ingredients]
    return similarity_dict_spacy

WARNING! FUNCTION BELOW WILL START THE PROCESS OF PREPARING SIMILARITIES MATRIX, DO NOT UNCOMMENT IT 

It take quite some time to calculate it

In [14]:
# testing_similarities                   = check_similarity(df_ingredients_vectorized.columns)
# ingredients_similarity_matrix          = pd.DataFrame(testing_similarities)
# ingredients_similarity_matrix['index'] = df_ingredients_vectorized.columns
# ingredients_similarity_matrix.set_index('index', inplace=True)
 
"""
CPU times: user 12h 1min 3s, sys: 2.76 s, total: 12h 1min 5s
Wall time: 12h 1min 3s
"""

'\nCPU times: user 12h 1min 3s, sys: 2.76 s, total: 12h 1min 5s\nWall time: 12h 1min 3s\n'

WARNING! DON'T UNCOMMENT THE LINE BELOW

In [15]:
# ingredients_similarity_matrix.to_pickle("ingredients_similarity_matrix.pkl")

Since similarity matrix is already calculated, only thing that we have to do is load it.

In [16]:
ingredients_similarity_matrix = pd.read_pickle("data/ingredients_similarity_matrix.pkl")

Let's just quickly take a look how the similarities for some random products looks like.

In [17]:
ingredients_similarity_matrix['czekolada'].sort_values(ascending=False).head(10)

index
czekolada     1.000000
czekoladka    0.876290
kawa          0.756586
szarlotka     0.749535
truskawka     0.745301
herbata       0.743748
pomarańcza    0.733977
galaretka     0.728852
wanilia       0.723134
kremówka      0.722154
Name: czekolada, dtype: float64

In [18]:
ingredients_similarity_matrix['kurczak'].sort_values(ascending=False).head(10)

index
kurczak      1.000000
indyk        0.740041
makaron      0.706092
łosoś        0.694199
ziemniak     0.693186
schab        0.693124
tuńczyk      0.691844
bakłażan     0.686526
burger       0.680588
pomidorek    0.675718
Name: kurczak, dtype: float64

In [19]:
ingredients_similarity_matrix['pomidor'].sort_values(ascending=False).head(10)

index
pomidor       1.000000
pomidorek     0.857178
ogórek        0.802565
ziemniak      0.735789
kalafior      0.724988
bakłażan      0.705871
rzodkiewka    0.684100
pomidorowy    0.683716
ananas        0.680346
szpinak       0.675247
Name: pomidor, dtype: float64

Although similar products for czekolada is not breath taking, outcomes for kurczak or pomidor are quite accurate. We will see if word2vec can give us something better or similar.

# 2. Word2Vec

Now we can find similarities using Word2Vec technique implemented in gensim package. Word2Vec is using a neural network model to find relationships between words in the text. It can be used to find synonymous. We can use it since we want to find ingredients that were used in a similar context - so in similar recipes.

parameters:
- window - max number of ingredients (just to be sure that we take into account all connections within a recipe)
- min_count - 1 - to include every product in the ingredients list
- I've experimented with small, medium, and large numbers, but a number of dimensions seems to change very little


## 2.1. Lematized ingredients - nouns only

For analysis I will use the lematized lists of words retrived from ingredients variable.

In [20]:
%%time

lematized_ingredients_nouns_list_merged = []

for _, row in df_working.iterrows():
    lematized_ingredients_nouns      = row.lematized_ingredients_nouns
    lematized_ingredients_nouns_list = lematized_ingredients_nouns.split(", ")
    lematized_ingredients_nouns_list_merged.append(lematized_ingredients_nouns_list)

model_ingredients_nouns = gensim.models.Word2Vec(lematized_ingredients_nouns_list_merged, 
                                                 window=30, 
                                                 min_count=2,
                                                 size=32)

CPU times: user 688 ms, sys: 20 ms, total: 708 ms
Wall time: 596 ms


In [21]:
model_ingredients_nouns.most_similar('czekolada')

/home/d0lar/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `most_similar` (Method will be removed in 4.0.0, use self.wv.most_similar() instead).
  """Entry point for launching an IPython kernel.


[('cukier', 0.9997270107269287),
 ('żółtko', 0.9996963739395142),
 ('mąka', 0.9995782971382141),
 ('żelatyna', 0.9994463920593262),
 ('laska', 0.9994176030158997),
 ('uht', 0.9994041919708252),
 ('kakao', 0.9993880987167358),
 ('budyń', 0.9989980459213257),
 ('malina', 0.9988781213760376),
 ('kryształ', 0.9983230829238892)]

In [22]:
model_ingredients_nouns.most_similar('kurczak', topn = 10)

/home/d0lar/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `most_similar` (Method will be removed in 4.0.0, use self.wv.most_similar() instead).
  """Entry point for launching an IPython kernel.


[('koperek', 0.9996099472045898),
 ('majonez', 0.9995747804641724),
 ('dymek', 0.9995182156562805),
 ('marchew', 0.9995067119598389),
 ('kmin', 0.9994996190071106),
 ('kapusta', 0.9994967579841614),
 ('fasola', 0.9994453191757202),
 ('pomidorek', 0.9994423389434814),
 ('ocet', 0.9994314908981323),
 ('szczypiorek', 0.9994235634803772)]

## 2.2. Lematized ingredients - nouns and adjectives

In [23]:
%%time

lematized_ingredients_list_merged = []

for _, row in df_working.iterrows():
    lematized_ingredients      = row.lematized_ingredients
    lematized_ingredients_list = lematized_ingredients.split(", ")
    lematized_ingredients_list_merged.append(lematized_ingredients_list)

model_ingredients = gensim.models.Word2Vec(lematized_ingredients_list_merged, 
                                           window=30, 
                                           min_count=2,
                                           size=32)

CPU times: user 902 ms, sys: 8.37 ms, total: 911 ms
Wall time: 736 ms


In [24]:
model_ingredients.most_similar('czekolada', topn = 10)

/home/d0lar/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `most_similar` (Method will be removed in 4.0.0, use self.wv.most_similar() instead).
  """Entry point for launching an IPython kernel.


[('kakao', 0.9997444748878479),
 ('puder', 0.9995988607406616),
 ('żelatyna', 0.9995779991149902),
 ('deserowy', 0.9995081424713135),
 ('cukier', 0.9992666244506836),
 ('białko', 0.9991178512573242),
 ('żółtko', 0.9991176724433899),
 ('malina', 0.9989913702011108),
 ('borówka', 0.9989421367645264),
 ('waniliowy', 0.9989314079284668)]

In [25]:
model_ingredients.most_similar('kurczak', topn = 10)

/home/d0lar/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `most_similar` (Method will be removed in 4.0.0, use self.wv.most_similar() instead).
  """Entry point for launching an IPython kernel.


[('słonecznikowy', 0.9997708201408386),
 ('koperek', 0.9997466802597046),
 ('bulion', 0.9997148513793945),
 ('marchew', 0.9996840357780457),
 ('szalotka', 0.9996572732925415),
 ('szczypiorek', 0.9996312260627747),
 ('fasola', 0.9996206760406494),
 ('ogórek', 0.9996078610420227),
 ('fileta', 0.9996042251586914),
 ('marchewka', 0.9995957612991333)]

## 2.3. Recipe instructions (just out of curiosity)

In [28]:
%%time

instructions_list_merged = []

for _, row in df_working.iterrows():
    instructions = row.instructions
    instructions_list = instructions.split()
    instructions_list_merged.append(instructions_list)

model_instructions = gensim.models.Word2Vec(instructions_list_merged, window=30, min_count=2,size=32)

CPU times: user 8.56 s, sys: 93.2 ms, total: 8.66 s
Wall time: 5.3 s


In [29]:
model_instructions.most_similar('czekolada', topn = 10)

/home/d0lar/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `most_similar` (Method will be removed in 4.0.0, use self.wv.most_similar() instead).
  """Entry point for launching an IPython kernel.


[('konsystencji', 0.9861382842063904),
 ('konsystencja', 0.9791234731674194),
 ('gęstej', 0.9760445952415466),
 ('rozrzedzić', 0.9718757271766663),
 ('Kiedy', 0.9704358577728271),
 ('masa', 0.9663467407226562),
 ('roztopienia', 0.9657214879989624),
 ('rozpuszczenia', 0.964694619178772),
 ('miękkie', 0.9646495580673218),
 ('rozpuści.', 0.9621611833572388)]

In [30]:
model_instructions.most_similar('kurczak', topn = 10)

/home/d0lar/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `most_similar` (Method will be removed in 4.0.0, use self.wv.most_similar() instead).
  """Entry point for launching an IPython kernel.


KeyError: "word 'kurczak' not in vocabulary"

To sum up - dataset is too small to train word2vec model properly. Returned results seems to be far from the products that we could consider as true replacements. The worest performance belongs to model based on recipe instructions. However, this is not a surprise, since there are a lot of verbs, which are useless for us. On top of that, all 3 models suffer from lack of some of the words.

## 1.1 Ngrams
Just befor main part, we can deep dive into connections between the products. Maybe we can find there some interesing things. To do that, we will use nltk package. ngrams shows how close words are used in text. We have here an order bias, but still, it may show us interesing dependencies.

In [31]:
sentences = (" ").join(df_working['lematized_ingredients_nouns'].tolist())
sentences = (" ").join(sentences.split(', '))

token     = nltk.word_tokenize(sentences)

bigrams_nouns   = Counter(ngrams(token, 2))
trigrams_nouns  = Counter(ngrams(token, 3))
fourgrams_nouns = Counter(ngrams(token, 4))
fivegrams_nouns = Counter(ngrams(token, 5))

In [32]:
print(bigrams_nouns)

Counter({('czosnek', 'oliwa'): 258, ('pomidor', 'oliwka'): 130, ('olej', 'masło'): 115, ('cynamon', 'cukier'): 108, ('cukier', 'puder'): 108, ('cytryna', 'cukier'): 98, ('papryka', 'czosnek'): 91, ('puder', 'czekolada'): 86, ('mąka', 'orzech'): 79, ('jajo', 'mąka'): 79, ('masło', 'śmietana'): 78, ('rozmiar', 'cukier'): 76, ('proszek', 'cukier'): 72, ('mąka', 'wanilia'): 70, ('pieczenie', 'masło'): 70, ('cebula', 'olej'): 64, ('masło', 'cukier'): 62, ('jajko', 'masło'): 61, ('mleko', 'masło'): 60, ('kakao', 'masło'): 59, ('uht', 'śmietanka'): 55, ('jajko', 'olej'): 54, ('ogórek', 'cebula'): 54, ('cebula', 'sok'): 54, ('cukier', 'jogurt'): 52, ('śmietanka', 'masło'): 52, ('masło', 'cytryna'): 49, ('olej', 'cytryna'): 49, ('żółtko', 'masło'): 49, ('l', 'mąka'): 47, ('jajko', 'śmietanka'): 46, ('śmietanka', 'żelatyna'): 46, ('cukier', 'opakowanie'): 46, ('mąka', 'jajko'): 44, ('czosnek', 'papryczka'): 44, ('sok', 'skórka'): 43, ('cukier', 'czekolada'): 43, ('oliwa', 'limonka'): 42, ('jajko

In [33]:
print(trigrams_nouns)

Counter({('papryka', 'czosnek', 'oliwa'): 38, ('cukier', 'puder', 'czekolada'): 37, ('czosnek', 'oliwa', 'limonka'): 25, ('jajko', 'pieczenie', 'masło'): 24, ('masło', 'cytryna', 'cukier'): 23, ('cukier', 'czosnek', 'oliwa'): 20, ('proszek', 'cynamon', 'cukier'): 20, ('mleko', 'żółtko', 'masło'): 19, ('pieczenie', 'kakao', 'masło'): 19, ('jogurt', 'czosnek', 'oliwa'): 18, ('masło', 'cynamon', 'cukier'): 18, ('rozmiar', 'cukier', 'puder'): 18, ('jajko', 'mleko', 'masło'): 17, ('cukier', 'jajo', 'mąka'): 17, ('proszek', 'rozmiar', 'cukier'): 17, ('cebula', 'sok', 'olej'): 16, ('uht', 'jajko', 'śmietanka'): 16, ('mleko', 'jajko', 'masło'): 16, ('cytryna', 'cynamon', 'cukier'): 15, ('cebula', 'olej', 'masło'): 15, ('czosnek', 'oliwa', 'bakłażan'): 15, ('proszek', 'cukier', 'puder'): 15, ('czosnek', 'oliwa', 'tymianek'): 14, ('masło', 'proszek', 'cukier'): 14, ('śmietanka', 'żelatyna', 'rozmiar'): 14, ('jajo', 'mąka', 'orzech'): 14, ('jajko', 'kakao', 'masło'): 14, ('sok', 'olej', 'cytryna'

In [34]:
print(fourgrams_nouns)

Counter({('uht', 'jajko', 'śmietanka', 'żelatyna'): 8, ('cebula', 'sok', 'olej', 'cytryna'): 7, ('mąka', 'wanilia', 'mleko', 'żółtko'): 7, ('mąka', 'pieczenie', 'mleko', 'masło'): 6, ('cukier', 'drożdże', 'jajo', 'mąka'): 6, ('wanilia', 'mleko', 'żółtko', 'masło'): 6, ('uht', 'śmietanka', 'żelatyna', 'rozmiar'): 6, ('pieczenie', 'kakao', 'masło', 'cukier'): 6, ('orzech', 'jajko', 'pieczenie', 'masło'): 6, ('cukier', 'jajo', 'mąka', 'orzech'): 6, ('mąka', 'orzech', 'jajko', 'pieczenie'): 6, ('czosnek', 'oliwa', 'limonka', 'natka'): 5, ('mąka', 'jajko', 'mleko', 'masło'): 5, ('jajko', 'mleko', 'masło', 'śmietana'): 5, ('pieczenie', 'masło', 'proszek', 'cukier'): 5, ('mleko', 'żółtko', 'masło', 'laska'): 5, ('sok', 'masło', 'cytryna', 'cukier'): 5, ('mąka', 'jajko', 'pieczenie', 'masło'): 5, ('cukier', 'puder', 'czekolada', 'l'): 5, ('olej', 'proszek', 'cynamon', 'cukier'): 5, ('jajko', 'śmietanka', 'żelatyna', 'rozmiar'): 5, ('migdał', 'jajko', 'pieczenie', 'masło'): 5, ('pieczenie', 'ma

In [35]:
print(fivegrams_nouns)

Counter({('mąka', 'wanilia', 'mleko', 'żółtko', 'masło'): 6, ('mąka', 'orzech', 'jajko', 'pieczenie', 'masło'): 5, ('jajko', 'pieczenie', 'masło', 'śmietanka', 'proszek'): 4, ('uht', 'jajko', 'śmietanka', 'żelatyna', 'rozmiar'): 4, ('pieczenie', 'masło', 'mleko', 'proszek', 'cukier'): 4, ('czosnek', 'oliwa', 'limonka', 'chili', 'skórka'): 3, ('wanilia', 'mleko', 'żółtko', 'masło', 'laska'): 3, ('pieczenie', 'olej', 'proszek', 'cynamon', 'cukier'): 3, ('mąka', 'orzech', 'pieczenie', 'jajko', 'masło'): 3, ('mąka', 'masło', 'orzech', 'pieczenie', 'kakao'): 3, ('czosnek', 'oliwa', 'pietruszka', 'tymianek', 'natka'): 2, ('oliwa', 'pietruszka', 'tymianek', 'natka', 'oliwka'): 2, ('papryczka', 'cebula', 'sok', 'olej', 'sos'): 2, ('sok', 'skórka', 'olej', 'dijon', 'cytryna'): 2, ('jogurt', 'czosnek', 'oliwa', 'sałata', 'kurczak'): 2, ('czosnek', 'oliwa', 'sałata', 'kurczak', 'pita'): 2, ('jogurt', 'czosnek', 'oliwa', 'orzeszek', 'limonka'): 2, ('cytryna', 'papryka', 'bakłażan', 'tymianek', 'cu

In [36]:
sentences = (" ").join(df_working['lematized_ingredients_nouns'].tolist())
sentences = (" ").join(sentences.split(', '))

token     = nltk.word_tokenize(sentences)

bigrams   = Counter(ngrams(token, 2))
trigrams  = Counter(ngrams(token, 3))
fourgrams = Counter(ngrams(token, 4))
fivegrams = Counter(ngrams(token, 5))

In [37]:
print(bigrams)

Counter({('czosnek', 'oliwa'): 258, ('pomidor', 'oliwka'): 130, ('olej', 'masło'): 115, ('cynamon', 'cukier'): 108, ('cukier', 'puder'): 108, ('cytryna', 'cukier'): 98, ('papryka', 'czosnek'): 91, ('puder', 'czekolada'): 86, ('mąka', 'orzech'): 79, ('jajo', 'mąka'): 79, ('masło', 'śmietana'): 78, ('rozmiar', 'cukier'): 76, ('proszek', 'cukier'): 72, ('mąka', 'wanilia'): 70, ('pieczenie', 'masło'): 70, ('cebula', 'olej'): 64, ('masło', 'cukier'): 62, ('jajko', 'masło'): 61, ('mleko', 'masło'): 60, ('kakao', 'masło'): 59, ('uht', 'śmietanka'): 55, ('jajko', 'olej'): 54, ('ogórek', 'cebula'): 54, ('cebula', 'sok'): 54, ('cukier', 'jogurt'): 52, ('śmietanka', 'masło'): 52, ('masło', 'cytryna'): 49, ('olej', 'cytryna'): 49, ('żółtko', 'masło'): 49, ('l', 'mąka'): 47, ('jajko', 'śmietanka'): 46, ('śmietanka', 'żelatyna'): 46, ('cukier', 'opakowanie'): 46, ('mąka', 'jajko'): 44, ('czosnek', 'papryczka'): 44, ('sok', 'skórka'): 43, ('cukier', 'czekolada'): 43, ('oliwa', 'limonka'): 42, ('jajko

In [38]:
print(trigrams)

Counter({('papryka', 'czosnek', 'oliwa'): 38, ('cukier', 'puder', 'czekolada'): 37, ('czosnek', 'oliwa', 'limonka'): 25, ('jajko', 'pieczenie', 'masło'): 24, ('masło', 'cytryna', 'cukier'): 23, ('cukier', 'czosnek', 'oliwa'): 20, ('proszek', 'cynamon', 'cukier'): 20, ('mleko', 'żółtko', 'masło'): 19, ('pieczenie', 'kakao', 'masło'): 19, ('jogurt', 'czosnek', 'oliwa'): 18, ('masło', 'cynamon', 'cukier'): 18, ('rozmiar', 'cukier', 'puder'): 18, ('jajko', 'mleko', 'masło'): 17, ('cukier', 'jajo', 'mąka'): 17, ('proszek', 'rozmiar', 'cukier'): 17, ('cebula', 'sok', 'olej'): 16, ('uht', 'jajko', 'śmietanka'): 16, ('mleko', 'jajko', 'masło'): 16, ('cytryna', 'cynamon', 'cukier'): 15, ('cebula', 'olej', 'masło'): 15, ('czosnek', 'oliwa', 'bakłażan'): 15, ('proszek', 'cukier', 'puder'): 15, ('czosnek', 'oliwa', 'tymianek'): 14, ('masło', 'proszek', 'cukier'): 14, ('śmietanka', 'żelatyna', 'rozmiar'): 14, ('jajo', 'mąka', 'orzech'): 14, ('jajko', 'kakao', 'masło'): 14, ('sok', 'olej', 'cytryna'

In [39]:
print(fourgrams)

Counter({('uht', 'jajko', 'śmietanka', 'żelatyna'): 8, ('cebula', 'sok', 'olej', 'cytryna'): 7, ('mąka', 'wanilia', 'mleko', 'żółtko'): 7, ('mąka', 'pieczenie', 'mleko', 'masło'): 6, ('cukier', 'drożdże', 'jajo', 'mąka'): 6, ('wanilia', 'mleko', 'żółtko', 'masło'): 6, ('uht', 'śmietanka', 'żelatyna', 'rozmiar'): 6, ('pieczenie', 'kakao', 'masło', 'cukier'): 6, ('orzech', 'jajko', 'pieczenie', 'masło'): 6, ('cukier', 'jajo', 'mąka', 'orzech'): 6, ('mąka', 'orzech', 'jajko', 'pieczenie'): 6, ('czosnek', 'oliwa', 'limonka', 'natka'): 5, ('mąka', 'jajko', 'mleko', 'masło'): 5, ('jajko', 'mleko', 'masło', 'śmietana'): 5, ('pieczenie', 'masło', 'proszek', 'cukier'): 5, ('mleko', 'żółtko', 'masło', 'laska'): 5, ('sok', 'masło', 'cytryna', 'cukier'): 5, ('mąka', 'jajko', 'pieczenie', 'masło'): 5, ('cukier', 'puder', 'czekolada', 'l'): 5, ('olej', 'proszek', 'cynamon', 'cukier'): 5, ('jajko', 'śmietanka', 'żelatyna', 'rozmiar'): 5, ('migdał', 'jajko', 'pieczenie', 'masło'): 5, ('pieczenie', 'ma

In [40]:
print(fivegrams)

Counter({('mąka', 'wanilia', 'mleko', 'żółtko', 'masło'): 6, ('mąka', 'orzech', 'jajko', 'pieczenie', 'masło'): 5, ('jajko', 'pieczenie', 'masło', 'śmietanka', 'proszek'): 4, ('uht', 'jajko', 'śmietanka', 'żelatyna', 'rozmiar'): 4, ('pieczenie', 'masło', 'mleko', 'proszek', 'cukier'): 4, ('czosnek', 'oliwa', 'limonka', 'chili', 'skórka'): 3, ('wanilia', 'mleko', 'żółtko', 'masło', 'laska'): 3, ('pieczenie', 'olej', 'proszek', 'cynamon', 'cukier'): 3, ('mąka', 'orzech', 'pieczenie', 'jajko', 'masło'): 3, ('mąka', 'masło', 'orzech', 'pieczenie', 'kakao'): 3, ('czosnek', 'oliwa', 'pietruszka', 'tymianek', 'natka'): 2, ('oliwa', 'pietruszka', 'tymianek', 'natka', 'oliwka'): 2, ('papryczka', 'cebula', 'sok', 'olej', 'sos'): 2, ('sok', 'skórka', 'olej', 'dijon', 'cytryna'): 2, ('jogurt', 'czosnek', 'oliwa', 'sałata', 'kurczak'): 2, ('czosnek', 'oliwa', 'sałata', 'kurczak', 'pita'): 2, ('jogurt', 'czosnek', 'oliwa', 'orzeszek', 'limonka'): 2, ('cytryna', 'papryka', 'bakłażan', 'tymianek', 'cu

All those ngrams could be used in finding product alternatives. It may be an idea for the future to use them, but for now, we will focus on spacy model, since it's polish language implementation seems to be much more efficient in comparison with word embeddings based on kuchnia lidla data.

# 3. Recipe matcher functions

It's not enough to create a similarity matrix. We need to implement it, so the user can pass the list of products and program will do the rest. So we need to start with finding if all ingredients included in the list are in the similarity matrix. If not, we need to add them.

In [41]:
ingredients_input = 'kurczak, czekolada, mąka, makaron, jajko, papryka'

In [42]:
def find_missing_ingredients(ingredients_input):
    missing_ingredients = []
    if type(ingredients_input) == str:
        ingredients_input = ingredients_input.split(", ")

    # check if all products are in similarity matrix
    for ingredient in ingredients_input:
        if ingredient not in ingredients_similarity_matrix:
            # add columns and rows so after getting similarity data they are the same lenght as colm and row
            ingredients_similarity_matrix[ingredient]     = 0
            ingredients_similarity_matrix.loc[ingredient] = pd.Series(0)
            missing_ingredients.append(ingredient)

            ingredient_similarity                         = [nlp(ingredient).similarity(nlp(i)) \
                                                             for i in ingredients_similarity_matrix.columns]
            # adding column
            ingredients_similarity_matrix[ingredient]     = ingredient_similarity
            # adding row
            ingredients_similarity_matrix.loc[ingredient] = ingredient_similarity
        else:
            print(f"{ingredient} ----------------available in the database")
    print(f'Ingredients added to database: {str(missing_ingredients)}')

In [43]:
find_missing_ingredients(ingredients_input)

kurczak ----------------available in the database
czekolada ----------------available in the database
mąka ----------------available in the database
makaron ----------------available in the database
jajko ----------------available in the database
papryka ----------------available in the database
Ingredients added to database: []


Since we want to expand the list of potential recipies to find, we have to create all possible combinations of products. Then we will pass it to the classifier and find the recipies with the highest match - highest probability. With the **min_number_of_ingredient** parameter, you can set the minimum len of the combination.

In [44]:
def make_ingredient_list_variants(ingredients_input, 
                                  min_number_of_ingredient=4):
    all_ingredient_combinations = []
    
    if type(ingredients_input) == str:
        ingredients_input = ingredients_input.split(", ")

    for r in range(len(ingredients_input)+1):
        combinations_list = list(combinations(ingredients_input, r))
        
        for i in combinations_list:
            if len(i) > min_number_of_ingredient:
                all_ingredient_combinations.append(list(i))
                
    return all_ingredient_combinations



In [45]:
make_ingredient_list_variants(ingredients_input)

[['kurczak', 'czekolada', 'mąka', 'makaron', 'jajko'],
 ['kurczak', 'czekolada', 'mąka', 'makaron', 'papryka'],
 ['kurczak', 'czekolada', 'mąka', 'jajko', 'papryka'],
 ['kurczak', 'czekolada', 'makaron', 'jajko', 'papryka'],
 ['kurczak', 'mąka', 'makaron', 'jajko', 'papryka'],
 ['czekolada', 'mąka', 'makaron', 'jajko', 'papryka'],
 ['kurczak', 'czekolada', 'mąka', 'makaron', 'jajko', 'papryka']]

We've done a similarity matrix for a purpose. We will use it to find alternatives of each product in the product list. To include only relevant products, **similarity_threshold** parameter should be used to set the minimal similarity level.

In [48]:
def get_ingredients_alternatives(ingredients_input, 
                                 similarity_threshold=0.8):
    alternatives_dict = {}
    
    if type(ingredients_input) == str:
        ingredients_input = ingredients_input.split(", ")

    for ingredient in ingredients_input:
        ranking = ingredients_similarity_matrix[ingredient][(ingredients_similarity_matrix[ingredient] != 1) & \
                                              (ingredients_similarity_matrix[ingredient] > similarity_threshold)] \
                                              .sort_values(ascending=False)
        alternatives_dict[ingredient] = ranking.index.tolist()

    return alternatives_dict

In [49]:
get_ingredients_alternatives(ingredients_input, similarity_threshold = 0.75)


{'kurczak': [],
 'czekolada': ['czekoladka', 'kawa'],
 'mąka': [],
 'makaron': ['makaronik', 'ryż'],
 'jajko': ['jajo'],
 'papryka': ['papryczka', 'cebula', 'cukinia']}

Now we can combine both lists and make all possible combinations including alternative products. Using that approach we will find eg. salad with tomato, while we have only paprika. But since this is similar product, product will return that recipe as well.

In [50]:
def combine_ingr_and_alt_into_combinations(ingredients_input, 
                                           similarity_threshold=0.75, 
                                           min_number_of_ingredient=5):
    if type(ingredients_input) == str:
        ingredients_input = ingredients_input.split(", ")
        
    alternatives                = [*get_ingredients_alternatives(ingredients_input, 
                                                  similarity_threshold = similarity_threshold)\
                                                  .values()]
    alternatives                = [item for sublist in alternatives for item in sublist]
    merged_list                 = alternatives + ingredients_input
    combinations_of_merged_list = make_ingredient_list_variants(set(merged_list), 
                                                                min_number_of_ingredient = min_number_of_ingredient)
    combinations_of_merged_list_len = len(combinations_of_merged_list)
    
    # since the number of combinations are increasing very fast with each additional element, 
    # this constrain is limiting the number of possible combinations. 
    # for larger lists it's getting a sample of 10000 combinations 
    if combinations_of_merged_list_len > 10000:
        return sample(combinations_of_merged_list, 10000)
    else:
        return combinations_of_merged_list

In [53]:
combine_ingr_and_alt_into_combinations(ingredients_input, 
                                       similarity_threshold=0.75, 
                                       min_number_of_ingredient=5)

[['papryka',
  'papryczka',
  'czekolada',
  'cukinia',
  'mąka',
  'jajko',
  'czekoladka'],
 ['czekolada',
  'jajo',
  'cukinia',
  'kurczak',
  'makaron',
  'cebula',
  'mąka',
  'ryż',
  'jajko',
  'czekoladka'],
 ['papryka',
  'czekolada',
  'jajo',
  'kawa',
  'cukinia',
  'kurczak',
  'ryż',
  'jajko',
  'czekoladka'],
 ['papryka',
  'papryczka',
  'czekolada',
  'kawa',
  'cukinia',
  'mąka',
  'ryż',
  'makaronik',
  'jajko',
  'czekoladka'],
 ['papryczka', 'jajo', 'kurczak', 'ryż', 'jajko', 'czekoladka'],
 ['papryka',
  'papryczka',
  'czekolada',
  'jajo',
  'kurczak',
  'makaron',
  'cebula',
  'ryż',
  'makaronik'],
 ['papryka', 'czekolada', 'kawa', 'cukinia', 'mąka', 'makaronik'],
 ['papryka',
  'papryczka',
  'czekolada',
  'jajo',
  'kurczak',
  'makaron',
  'mąka',
  'jajko'],
 ['papryka', 'jajo', 'cukinia', 'kurczak', 'makaronik', 'jajko'],
 ['papryczka',
  'cukinia',
  'makaron',
  'ryż',
  'makaronik',
  'jajko',
  'czekoladka'],
 ['papryka',
  'papryczka',
  'czeko

# 3. Classifier

Noe we need to prepare our simple classifier. Since we have very limited number of recipes, we will do a simple trick. For each recipe we will take one ingredient out and leave others. That excercise will be repeated for every item in the ingredient list. So let's prepare a dataset.

## 3.1. Classifier based on ingredients with both adjectives and nouns

We will start with our dataframe with lematized ingredients where we have both nouns and adjectives

In [54]:
# To achieve that I've use a piece of code prepared by Bartosz Mikulski
# https://www.mikulskibartosz.name/how-to-split-a-list-inside-a-dataframe-cell-into-rows-in-pandas/
missing_ingredient_list    = []
meal_type_list             = []
link_list                  = []
rest_of_ingredients_list   = []
meal_type_detailed_list    = []
raw_ingredients_list       = []
lematized_ingredients_list = []

for _, row in df_working.iterrows():
    meal_type             = row.meal_type
    link                  = row.link
    meal_type_detailed    = row.meal_type_detailed
    raw_ingredients       = row.ingredients
    lematized_ingredients = row.lematized_ingredients
    
    for ingredient in row.lematized_ingredients.split(", "):
        meal_type_list.append(meal_type)
        missing_ingredient_list.append(ingredient)
        link_list.append(link)
        rest_of_ingredients_list.append(", ".join([x for x in row.lematized_ingredients.split(", ") \
                                                   if x!=ingredient]))
        meal_type_detailed_list.append(meal_type_detailed)
        raw_ingredients_list.append(raw_ingredients)
        lematized_ingredients_list.append(lematized_ingredients)

df_missing_ingr_clf = pd.DataFrame({
    "link"                 : link_list,
    "lematized_ingredients": lematized_ingredients_list,
    "missing_ingredient"   : missing_ingredient_list,
    "meal_type_list"       : meal_type_list,
    "rest_of_ingredients"  : rest_of_ingredients_list,
    "meal_type_detailed"   : meal_type_detailed_list,
    "raw_ingredients_list" :raw_ingredients_list,
})

df_missing_ingr_clf

link  \
0      /ravioli-z-cukinia-i-ricotta   
1      /ravioli-z-cukinia-i-ricotta   
2      /ravioli-z-cukinia-i-ricotta   
3      /ravioli-z-cukinia-i-ricotta   
4      /ravioli-z-cukinia-i-ricotta   
...                             ...   
40498              /mus-czekoladowy   
40499              /mus-czekoladowy   
40500              /mus-czekoladowy   
40501              /mus-czekoladowy   
40502              /mus-czekoladowy   

                                   lematized_ingredients missing_ingredient  \
0      czosnek, oliwa, winogrono, semolina, chili, pe...            czosnek   
1      czosnek, oliwa, winogrono, semolina, chili, pe...              oliwa   
2      czosnek, oliwa, winogrono, semolina, chili, pe...          winogrono   
3      czosnek, oliwa, winogrono, semolina, chili, pe...           semolina   
4      czosnek, oliwa, winogrono, semolina, chili, pe...              chili   
...                                                  ...                ...   
40498  czekolada, carre, gorzki, fin, mleczny, śmieta...             gorzki   
40499  czekolada, carre, gorzki, fin, mleczny, śmieta...                fin   
40500  czekolada, carre, gorzki, fin, mleczny, śmieta...            mleczny   
40501  czekolada, carre, gorzki, fin, mleczny, śmieta...          śmietanka   
40502  czekolada, carre, gorzki, fin, mleczny, śmieta...              pilos   

      meal_type_list                                rest_of_ingredients  \
0             glowne  oliwa, winogrono, semolina, chili, pestka, tor...   
1             glowne  czosnek, winogrono, semolina, chili, pestka, t...   
2             glowne  czosnek, oliwa, semolina, chili, pestka, torto...   
3             glowne  czosnek, oliwa, winogrono, chili, pestka, tort...   
4             glowne  czosnek, oliwa, winogrono, semolina, pestka, t...   
...              ...                                                ...   
40498         desery   czekolada, carre, fin, mleczny, śmietanka, pilos   
40499         desery  czekolada, carre, gorzki, mleczny, śmietanka, ...   
40500         desery    czekolada, carre, gorzki, fin, śmietanka, pilos   
40501         desery      czekolada, carre, gorzki, fin, mleczny, pilos   
40502         desery  czekolada, carre, gorzki, fin, mleczny, śmietanka   

       meal_type_detailed                               raw_ingredients_list  
0               Bez mięsa  cukinia – 1 szt., oliwa z oliwek – 1 łyżka, cz...  
1               Bez mięsa  cukinia – 1 szt., oliwa z oliwek – 1 łyżka, cz...  
2               Bez mięsa  cukinia – 1 szt., oliwa z oliwek – 1 łyżka, cz...  
3               Bez mięsa  cukinia – 1 szt., oliwa z oliwek – 1 łyżka, cz...  
4               Bez mięsa  cukinia – 1 szt., oliwa z oliwek – 1 łyżka, cz...  
...                   ...                                                ...  
40498  Desery czekoladowe  śmietanka Pilos 30%, mocno schłodzona: 300 ml,...  
40499  Desery czekoladowe  śmietanka Pilos 30%, mocno schłodzona: 300 ml,...  
40500  Desery czekoladowe  śmietanka Pilos 30%, mocno schłodzona: 300 ml,...  
40501  Desery czekoladowe  śmietanka Pilos 30%, mocno schłodzona: 300 ml,...  
40502  Desery czekoladowe  śmietanka Pilos 30%, mocno schłodzona: 300 ml,...  

[40503 rows x 7 columns]

Since we will not predict unnknown recipies we will use the whole dataset. It's not a surprise that the accuracy is so high, since there is a data leak. But we do not worry about it, since this classifier is used for a different purpose than normal.

In [73]:
%%time
X_train, X_test, y_train, y_test = train_test_split(df_missing_ingr_clf['rest_of_ingredients'], 
                                                    df_missing_ingr_clf['link'], 
                                                    test_size=0.1, 
                                                    random_state=42)

pipe = Pipeline([("vectorizer", CountVectorizer(analyzer  = 'word', 
                                                tokenizer = lambda x: x.split(", "))),
                 ("regresja", LogisticRegression(solver   = "liblinear"))])
pipe.fit(df_missing_ingr_clf['lematized_ingredients'], 
         df_missing_ingr_clf['link'])

accuracy_score(pipe.predict(X_test), y_test)

# Model need to be run, because can't pickle lambda funciton
# https://stackoverflow.com/questions/25348532/can-python-pickle-lambda-functions/25353243#25353243

CPU times: user 7min 13s, sys: 78.9 ms, total: 7min 13s
Wall time: 7min 13s


0.9997531473710195

In [74]:
ingredients_input = 'kurczak, czekolada, mąka, makaron, jajko, papryka'
find_missing_ingredients(ingredients_input)

ingredients_combinations_test = combine_ingr_and_alt_into_combinations(ingredients_input, 
                                                                       similarity_threshold=0.75,
                                                                       min_number_of_ingredient=5)

ingredients_combinations_test = [", ".join(i) for i in ingredients_combinations_test]

get_ingredients_alternatives(ingredients_input, 
                             similarity_threshold=0.75)

kurczak ----------------available in the database
czekolada ----------------available in the database
mąka ----------------available in the database
makaron ----------------available in the database
jajko ----------------available in the database
papryka ----------------available in the database
Ingredients added to database: []


{'kurczak': [],
 'czekolada': ['czekoladka', 'kawa'],
 'mąka': [],
 'makaron': ['makaronik', 'ryż'],
 'jajko': ['jajo'],
 'papryka': ['papryczka', 'cebula', 'cukinia']}

In [75]:
result_alt          ={}
combination         =[]
probability         =[]
result_alt          =[]
recipe              =[]
missing_ingredients =[]

predi = pipe.predict_proba(ingredients_combinations_test)

for idx,p in enumerate(predi):
    list_of_predictions = list(zip(list(pipe.classes_), predi[idx,:]))
    list_of_predictions = pd.DataFrame(list_of_predictions)
    list_of_predictions = list_of_predictions.sort_values(by=[1], ascending=False)\
                                             .head(1)\
                                             .values\
                                             .tolist()
    combination.append(ingredients_combinations_test[idx])
    recipe.append(list_of_predictions[0][0])
    probability.append(list_of_predictions[0][1])
    result_alt = {"index"      : combination, 
                  'recipe'     :recipe, 
                  'probability':probability}
    
list_of_proposed_recipes = pd.DataFrame.from_dict(result_alt)
list_of_proposed_recipes.sort_values(by=['probability'],
                                     ascending=False)
list_of_proposed_recipes = list_of_proposed_recipes['recipe'].drop_duplicates()\
                                                             .head(5)\
                                                             .tolist()

alternatives = get_ingredients_alternatives(ingredients_input,
                                            similarity_threshold=0.75)

from pprint import pprint
print('Alternatives:')
pprint(alternatives)

for i in list_of_proposed_recipes:
    recipe_name        = df_working.loc[df_working['link'] == i]['recipe_name'].drop_duplicates().tolist()[0]
    link               = df_working.loc[df_working['link'] == i]['link'].drop_duplicates().tolist()[0]
    meal_type_detailed = df_working.loc[df_working['link'] == i]['meal_type_detailed'].drop_duplicates().tolist()[0]
    raw_ingredients    = df_working.loc[df_working['link'] == i]['raw_ingredients'].drop_duplicates().tolist()[0]
    instructions       = df_working.loc[df_working['link'] == i]['instructions'].drop_duplicates().tolist()[0]

    print('-------------------\n')
    print(recipe_name)
    print(f'Meal category: {meal_type_detailed}')
    print(f'See more on: https://kuchnialidla.pl{link}\n')
    print(f'Ingredients list: {raw_ingredients}')
    print('Instructions:')
    print(instructions)

Alternatives:
{'czekolada': ['czekoladka', 'kawa'],
 'jajko': ['jajo'],
 'kurczak': [],
 'makaron': ['makaronik', 'ryż'],
 'mąka': [],
 'papryka': ['papryczka', 'cebula', 'cukinia']}
-------------------

Smażone kuleczki z cukinii
Meal category: Przekąski na imprezę
See more on: https://kuchnialidla.pl/smazone-kuleczki-z-cukinii

Ingredients list: 500 g cukinii, 100 g sera feta, 1/2 cebuli, 100 g sera grana padano, 3 łyżki posiekanej pietruszki, 1 łyżka oregano, 2 jajka, 1/2 szklanki bułki tartej, 1/2 szklanki mąki, Sól, Pieprz, 1 l oleju
Instructions:
 Przygotowanie W garnku zagotowujemy wodę. Cukinię trzemy na tarce o grubych oczkach i przekładamy na sito, kt&#243;re następnie zanurzamy we wrzącej wodzie na około 2 minuty. Wyjmujemy, odcedzamy, a gdy cukinia lekko przestygnie dobrze odciskamy ją z nadmiaru wody. Na patelni rozgrzewamy 1 łyżkę oleju. Cebulę drobno siekamy, wrzucamy na patelnię, solimy i smażymy do zeszklenia. Przekładamy do dużej miski. Dodajemy cukinię, pietruszkę, o

## 3.2. Classifier based on ingredients with nouns only

Now, let's compare it to the result that will be return based on the model where we have only nouns as ingredients.

In [66]:
missing_ingredient_list    = []
meal_type_list             = []
link_list                  = []
rest_of_ingredients_list   = []
meal_type_detailed_list    = []
raw_ingredients_list       = []
lematized_ingredients_list = []

for _, row in df_working.iterrows():
    meal_type             = row.meal_type
    link                  = row.link
    meal_type_detailed    = row.meal_type_detailed
    raw_ingredients       = row.ingredients
    lematized_ingredients = row.lematized_ingredients_nouns
    
    for ingredient in row.lematized_ingredients_nouns.split(", "):
        meal_type_list.append(meal_type)
        missing_ingredient_list.append(ingredient)
        link_list.append(link)
        rest_of_ingredients_list.append(", ".join([x for x in row.lematized_ingredients_nouns.split(", ") \
                                                   if x!=ingredient]))
        meal_type_detailed_list.append(meal_type_detailed)
        raw_ingredients_list.append(raw_ingredients)
        lematized_ingredients_list.append(lematized_ingredients)

df_missing_ingr_nouns_clf = pd.DataFrame({
    "link"                       : link_list,
    "lematized_ingredients_nouns": lematized_ingredients_list,
    "missing_ingredient_noun"    : missing_ingredient_list,
    "meal_type_list"             : meal_type_list,
    "rest_of_ingredients_nouns"  : rest_of_ingredients_list,
    "meal_type_detailed"         : meal_type_detailed_list,
    "raw_ingredients_list"       : raw_ingredients_list,
})

df_missing_ingr_nouns_clf

link  \
0      /ravioli-z-cukinia-i-ricotta   
1      /ravioli-z-cukinia-i-ricotta   
2      /ravioli-z-cukinia-i-ricotta   
3      /ravioli-z-cukinia-i-ricotta   
4      /ravioli-z-cukinia-i-ricotta   
...                             ...   
30050              /mus-czekoladowy   
30051              /mus-czekoladowy   
30052              /mus-czekoladowy   
30053              /mus-czekoladowy   
30054              /mus-czekoladowy   

                             lematized_ingredients_nouns  \
0      pestka, czosnek, oliwa, ricotta, parmezan, win...   
1      pestka, czosnek, oliwa, ricotta, parmezan, win...   
2      pestka, czosnek, oliwa, ricotta, parmezan, win...   
3      pestka, czosnek, oliwa, ricotta, parmezan, win...   
4      pestka, czosnek, oliwa, ricotta, parmezan, win...   
...                                                  ...   
30050            czekolada, carre, fin, śmietanka, pilos   
30051            czekolada, carre, fin, śmietanka, pilos   
30052            czekolada, carre, fin, śmietanka, pilos   
30053            czekolada, carre, fin, śmietanka, pilos   
30054            czekolada, carre, fin, śmietanka, pilos   

      missing_ingredient_noun meal_type_list  \
0                      pestka         glowne   
1                     czosnek         glowne   
2                       oliwa         glowne   
3                     ricotta         glowne   
4                    parmezan         glowne   
...                       ...            ...   
30050               czekolada         desery   
30051                   carre         desery   
30052                     fin         desery   
30053               śmietanka         desery   
30054                   pilos         desery   

                               rest_of_ingredients_nouns  meal_type_detailed  \
0      czosnek, oliwa, ricotta, parmezan, winogrono, ...           Bez mięsa   
1      pestka, oliwa, ricotta, parmezan, winogrono, c...           Bez mięsa   
2      pestka, czosnek, ricotta, parmezan, winogrono,...           Bez mięsa   
3      pestka, czosnek, oliwa, parmezan, winogrono, c...           Bez mięsa   
4      pestka, czosnek, oliwa, ricotta, winogrono, cu...           Bez mięsa   
...                                                  ...                 ...   
30050                       carre, fin, śmietanka, pilos  Desery czekoladowe   
30051                   czekolada, fin, śmietanka, pilos  Desery czekoladowe   
30052                 czekolada, carre, śmietanka, pilos  Desery czekoladowe   
30053                       czekolada, carre, fin, pilos  Desery czekoladowe   
30054                   czekolada, carre, fin, śmietanka  Desery czekoladowe   

                                    raw_ingredients_list  
0      cukinia – 1 szt., oliwa z oliwek – 1 łyżka, cz...  
1      cukinia – 1 szt., oliwa z oliwek – 1 łyżka, cz...  
2      cukinia – 1 szt., oliwa z oliwek – 1 łyżka, cz...  
3      cukinia – 1 szt., oliwa z oliwek – 1 łyżka, cz...  
4      cukinia – 1 szt., oliwa z oliwek – 1 łyżka, cz...  
...                                                  ...  
30050  śmietanka Pilos 30%, mocno schłodzona: 300 ml,...  
30051  śmietanka Pilos 30%, mocno schłodzona: 300 ml,...  
30052  śmietanka Pilos 30%, mocno schłodzona: 300 ml,...  
30053  śmietanka Pilos 30%, mocno schłodzona: 300 ml,...  
30054  śmietanka Pilos 30%, mocno schłodzona: 300 ml,...  

[30055 rows x 7 columns]

In [70]:
%%time
X_train, X_test, y_train, y_test = train_test_split(df_missing_ingr_nouns_clf['rest_of_ingredients_nouns'], 
                                                    df_missing_ingr_nouns_clf['link'], 
                                                    test_size=0.1, 
                                                    random_state=42)


pipe_nouns = Pipeline([
                        ("vectorizer", CountVectorizer(analyzer='word', tokenizer=lambda x: x.split(", "))),
                        # ("scaler", StandardScaler(with_mean=False)),
                        # ("normalizer", Normalizer()),
                        ("regresja", LogisticRegression(solver="liblinear"))])
pipe_nouns.fit(df_working['lematized_ingredients'], df_working['link'])

accuracy_score(pipe_nouns.predict(X_test), y_test)

# Model need to be run, because can't pickle lambda funciton
# https://stackoverflow.com/questions/25348532/can-python-pickle-lambda-functions/25353243#25353243

CPU times: user 20.1 s, sys: 84 ms, total: 20.2 s
Wall time: 20.2 s


0.9986693280106453

In [71]:
ingredients_input = 'kurczak, czekolada, mąka, makaron, jajko, papryka'
find_missing_ingredients(ingredients_input)

ingredients_combinations_test = combine_ingr_and_alt_into_combinations(ingredients_input, 
                                                                       similarity_threshold=0.75, 
                                                                       min_number_of_ingredient=5)

ingredients_combinations_test = [", ".join(i) for i in ingredients_combinations_test]

get_ingredients_alternatives(ingredients_input, 
                             similarity_threshold=0.75)

kurczak ----------------available in the database
czekolada ----------------available in the database
mąka ----------------available in the database
makaron ----------------available in the database
jajko ----------------available in the database
papryka ----------------available in the database
Ingredients added to database: []


{'kurczak': [],
 'czekolada': ['czekoladka', 'kawa'],
 'mąka': [],
 'makaron': ['makaronik', 'ryż'],
 'jajko': ['jajo'],
 'papryka': ['papryczka', 'cebula', 'cukinia']}

In [72]:
result_alt          = {}
combination         = []
probability         = []
result_alt          = []
recipe              = []
missing_ingredients = []

prediction_nouns = pipe_nouns.predict_proba(ingredients_combinations_test)

for idx,p in enumerate(prediction_nouns):
    list_of_predictions = list(zip(list(pipe_nouns.classes_), prediction_nouns[idx,:]))
    list_of_predictions = pd.DataFrame(list_of_predictions)
    list_of_predictions = list_of_predictions.sort_values(by=[1], ascending=False).head(1).values.tolist()
    combination.append(ingredients_combinations_test[idx])
    recipe.append(list_of_predictions[0][0])
    probability.append(list_of_predictions[0][1])
    result_alt = {"index"      : combination, 
                  'recipe'     : recipe, 
                  'probability': probability}

list_of_proposed_recipes = pd.DataFrame.from_dict(result_alt)
list_of_proposed_recipes.sort_values(by=['probability'], ascending=False)
list_of_proposed_recipes = list_of_proposed_recipes['recipe'].drop_duplicates()\
                                                             .head(5)\
                                                             .tolist()
alternatives = get_ingredients_alternatives(ingredients_input, 
                                            similarity_threshold=0.75)

from pprint import pprint
print('Alternatives:')
pprint(alternatives)
for i in list_of_proposed_recipes:
    recipe_name           = df_working.loc[df_working['link'] == i]['recipe_name'].drop_duplicates().tolist()[0]
    link                  = df_working.loc[df_working['link'] == i]['link'].drop_duplicates().tolist()[0]
    meal_type_detailed    = df_working.loc[df_working['link'] == i]['meal_type_detailed'].drop_duplicates().tolist()[0]
    raw_ingredients       = df_working.loc[df_working['link'] == i]['raw_ingredients'].drop_duplicates().tolist()[0]
    instructions          = df_working.loc[df_working['link'] == i]['instructions'].drop_duplicates().tolist()[0]
    lematized_ingredients = df_working.loc[df_working['link'] == i]['lematized_ingredients_nouns'].drop_duplicates().tolist()[0]
        
    print('-------------------\n')
    print(recipe_name)
    print(f'Meal category: {meal_type_detailed}')
    print(f'See more on: https://kuchnialidla.pl{link}\n')
    print(f'Ingredients list: {raw_ingredients}')
    print('Instructions:')
    print(instructions)
    

Alternatives:
{'czekolada': ['czekoladka', 'kawa'],
 'jajko': ['jajo'],
 'kurczak': [],
 'makaron': ['makaronik', 'ryż'],
 'mąka': [],
 'papryka': ['papryczka', 'cebula', 'cukinia']}
-------------------

Kolorowe naleśniczki
Meal category: Naleśniki na słono
See more on: https://kuchnialidla.pl/kolorowe-nalesniczki

Ingredients list: pierś kurczaka – 1 szt., czosnek – 1 ząbek, cebula – 1 szt., papryka – 0,5 szt., cukinia – 1 szt., ser żółty – 100 g, sól – 1 szczypta, pieprz – 1 szczypta, kmin rzymski, mielony – 1 szczypta, imbir, mielony – 0,5 łyżeczki, oliwa z oliwek do smażenia, masło – 1 łyżka, mleko – 200 ml, woda – 80 ml, mąka pszenna – 150 g, jaja – 1 szt., kurkuma, mielona – 1 łyżeczka, szpinak – 1 garść, natka pietruszki, oliwa z oliwek do smażenia
Instructions:
 Przygotuj mikser piekarnik rozgrzany do temperatury 180&#176;C Krok 1: Podsmażamy farsz Mięso kroimy w cienkie paseczki, doprawiamy solą, pieprzem i obsmażamy na patelni z dodatkiem oliwy. Czosnek i cebulę drobno sieka

# Summary
As an exploration of possible approaches to create recipes matcher, this project confirmed that processing of polish language is not an easy task. Fortunately, there is a package like Spacy with the implemented polish model (thanks to Ryszard Tuora). That helped in finding the same words in different forms, so they are not separate tokens. However, diminutives are considered as different words in comparison to base form (pomidor vs. pomidorek). Using the classifier as a recommending system was not a good choice, although recipes returned by the model are more or less appropriate. Both models however are skewed if they found any match. I tried using StandardScaler to minimize the effect of words with high frequency and also Normalizer to lower the impact of recipes with a high number of ingredients (that increases the chance of being picked), but I notice no significant change in terms of fitting accuracy. I did not use any of the well-known accuracy metrics, because they are simply not useful while browsing the given recipes. However, this tool returns something that in general can give a user idea of a dish possible to create. 

# Areas of improvement
- Dataset should be cleaned better.
- Code and function performance should be improved
- Logistic regression for binary data is not the best choice
- better usage of ngrams
- Explore more word2vec technique
- Detailed analysis of the recipes and ingredients is needed
- Better coding practicies
- Numpy usage for cosine similarity calculation (much more efficient)